In [5]:
import requests
import base64
import time

In [9]:
# API endpoint
BASE_URL = "http://127.0.0.1:7960"

def generate_no_preview(image_base64: str):
    """Generate 3D model from a single base64-encoded image without previews.
    
    Args:
        image_base64: Base64 string of the image (without 'data:image/...' prefix)
    """
    try:
        # Set generation parameters
        params = {
            'image_base64': image_base64,
            'seed': 42,
            'ss_guidance_strength': 7.5,
            'ss_sampling_steps': 30,
            'slat_guidance_strength': 7.5,
            'slat_sampling_steps': 30,
            'mesh_simplify_ratio': 0.95,
            'texture_size': 1024,
            'output_format': 'glb'
        }
        
        # Start generation
        print("Starting generation...")
        response = requests.post(f"{BASE_URL}/generate_no_preview", data=params)
        response.raise_for_status()
        
        # Poll status until complete
        while True:
            status = requests.get(f"{BASE_URL}/status").json()
            print(f"Progress: {status['progress']}%")
            
            if status['status'] == 'COMPLETE':
                break
            elif status['status'] == 'FAILED':
                raise Exception(f"Generation failed: {status['message']}")
            
            time.sleep(1)
        
        # Download the model
        print("Downloading model...")
        response = requests.get(f"{BASE_URL}/download/model")
        response.raise_for_status()
        print("Model downloaded.")
        
        return response.content
        
    except Exception as e:
        print(f"Error: {str(e)}")
        return None

In [10]:

image_path = '../images/2025-10-24-11-55-38.jpg'

with open(image_path, 'rb') as image_file:
    image_data = image_file.read()

base64_encoded = base64.b64encode(image_data).decode('utf-8')
print(base64_encoded)


...


In [13]:
model = generate_no_preview(base64_encoded)
print(model)

Starting generation...
Progress: 100%
Model downloaded.
b'glTF\x02\x00\x00\x00h\xd3\x15\x00(\x05\x00\x00JSON{"scene":0,"scenes":[{"nodes":[0]}],"asset":{"version":"2.0","generator":"https://github.com/mikedh/trimesh"},"accessors":[{"componentType":5125,"type":"SCALAR","bufferView":0,"count":12411,"max":[3302],"min":[0]},{"componentType":5126,"type":"VEC3","byteOffset":0,"bufferView":1,"count":3303,"max":[0.26851367950439453,0.4996616542339325,0.08201231062412262],"min":[-0.2682398557662964,-0.4997158348560333,-0.08280301094055176]},{"componentType":5126,"type":"VEC2","byteOffset":0,"bufferView":3,"count":3303,"max":[0.9994686245918274,0.9994419813156128],"min":[0.0005313496221788228,0.000558018684387207]}],"meshes":[{"name":"geometry_0","extras":{"processed":true},"primitives":[{"attributes":{"POSITION":1,"TEXCOORD_0":2},"indices":0,"mode":4,"material":0}]}],"images":[{"bufferView":2,"mimeType":"image/png"}],"textures":[{"source":0}],"materials":[{"pbrMetallicRoughness":{"baseColorText

In [14]:
output_path = "../models/model_test.glb"

with open(output_path, 'wb') as f:
    f.write(model)
print(f"Model saved to {output_path}")


Model saved to ../models/model_test.glb
